In [7]:
import numpy as np
from sklearn.discriminant_analysis import LinearDiscriminantAnalysis as LDA

import sys
sys.path.append('../')
import scripts.map_and_average as mapper
import scripts.util_feature_learning as util_feature_learning

## Load data

In [8]:
trainset, valset, testset = mapper.load_train_val_test_sets()
traindata, trainlabels, trainaudiolabels = trainset
valdata, vallabels, valaudiolabels = valset
testdata, testlabels, testaudiolabels = testset
labels = np.concatenate((trainlabels, vallabels, testlabels)).ravel()
audiolabels = np.concatenate((trainaudiolabels, valaudiolabels, testaudiolabels)).ravel()
print traindata.shape, valdata.shape, testdata.shape

/import/c4dm-04/mariap/train_data_melodia_8.pickle


IOError: [Errno 2] No such file or directory: '/import/c4dm-04/mariap/train_data_melodia_8.pickle'

## explain LDA

In [ ]:
min_variance = 0.99
feat_labels, feat_inds = mapper.get_feat_inds(n_dim=traindata.shape[1])
for i in range(len(feat_inds)):
    print "mapping " + feat_labels[i]
    inds = feat_inds[i]
    ssm_feat = util_feature_learning.Transformer()
    if min_variance is not None:
        ssm_feat.fit_data(traindata[:, inds], trainlabels, n_components=len(inds), pca_only=True)
        n_components = np.where(ssm_feat.pca_transformer.explained_variance_ratio_.cumsum()>min_variance)[0][0]+1
        print n_components, len(inds)
        ssm_feat.fit_lda_data(traindata[:, inds], trainlabels, n_components=n_components)

        WW = ssm_feat.lda_transformer.scalings_
        plt.figure()
        plt.imshow(WW[:, :n_components].T, aspect='auto')
        plt.colorbar()

## explain classifier

In [ ]:
X_list, Y, Yaudio = pickle.load(open('../data/lda_data_melodia_8.pickle','rb'))
Xrhy, Xmel, Xmfc, Xchr = X_list
X = np.concatenate((Xrhy, Xmel, Xmfc, Xchr), axis=1)

In [ ]:
ssm_feat.classify_and_save(X_train, Y_train, X_test, Y_test, transform_label=" ")

In [ ]:
def components_plot(lda_transformer, XX, n_comp=42, figurename=None):
    WW=lda_transformer.scalings_
    Xlda=lda_transformer.transform(XX)
    Xww=numpy.dot(XX, WW[:, :n_comp])
    plt.figure()
    plt.imshow(Xlda - Xww, aspect='auto')
    plt.figure()
    plt.imshow(Xlda, aspect='auto')
    plt.figure()
    plt.imshow(Xww, aspect='auto')
    plt.figure()
    plt.imshow(WW[:, :n_comp], aspect='auto') # this explains the weights up to n_components=64
    if figurename is not None:
        plt.savefig(figurename)

XX = traindata[:, inds]
components_plot(ssm_feat.lda_transformer, XX, n_comp=n_components)